In [1]:
from numpy import *
from numpy.linalg import norm
from wgs84tolocal import *
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot, plot
init_notebook_mode(connected=True)
%matplotlib inline

In [2]:
# Sphere settings
RADIUS = RADIUS_KM
LINES = 120
RESOLUTION = 120

# Subspace settings
SIDE = RADIUS / 300

# Axes settings
AXES_LEN = RADIUS

# Problem settings
SCALE = 1
CITIES = {
    'Melbourne': (-37.8140000, 144.9633200),
    'Sydney': (-33.8678500, 151.2073200),
    'Perth': (-31.9522400, 115.8614000),
    'San Francisco': (37.773972, -122.431297),
    'New York': (40.730610, -73.935242),
    'Washington': (38.8951100, -77.0363700),
    'Austin': (30.2671500, -97.7430600),
    'North Pole': (90, 0)
}
CITY1, CITY2 = 'Austin', 'New York'

In [3]:
def draw_subspace(transf_matrix):
    def gen_points(points, transf_matrix):
        points = transf_matrix @ points
        line_params = {'mode': 'lines', 'showlegend': False, 'line': go.scatter3d.Line(color='#999', width=2)}
        return go.Scatter3d(x=points[0,:], y=points[1,:], z=points[2,:], **line_params)
        
    city1 = lla_to_wgs84(CITIES[CITY1][0], CITIES[CITY1][1])
    city2 = lla_to_wgs84(CITIES[CITY2][0], CITIES[CITY2][1])
    city1 = list(city1) + [1]
    city2 = list(city2) + [1]
    x_span, y_span, _, _ = abs(transf_matrix.T @ city1 - transf_matrix.T @ city2)
    x_span = arange(-x_span/2, +x_span/2, SIDE)
    y_span = arange(-y_span/2, +y_span/2, SIDE)
    
    xv, yv = meshgrid(x_span, y_span)
    zv = zeros_like(xv)
    tv = ones_like(xv)
    traces = []
    for x, y, z, t in zip(xv, yv, zv, tv):
        points = vstack([x, y, z, t])
        traces.append(gen_points(points, transf_matrix))
    for x, y, z, t in zip(xv.T, yv.T, zv.T, tv.T):
        points = vstack([x.T, y.T, z.T, t.T])
        traces.append(gen_points(points, transf_matrix))
    
    return traces

def draw_axes(transf_matrix):
    traces = []
    line_params = {'mode': 'lines', 'showlegend': False}
    px = transf_matrix @ array([[0,0,0,1],[AXES_LEN,0,0,1]]).T
    py = transf_matrix @ array([[0,0,0,1],[0,AXES_LEN,0,1]]).T
    pz = transf_matrix @ array([[0,0,0,1],[0,0,AXES_LEN,1]]).T
    f = lambda points, color: go.Scatter3d(x=px[0,:], y=px[1,:], z=px[2,:],
                                           name='X', line=go.scatter3d.Line(color=color, width=3),
                                           mode='lines', showlegend=False)
    traces = [f(px, '#F00'),
              f(py, '#0F0'),
              f(pz, '#00F')]
    
    return traces

def draw_markers(x, y, z, name):
    return go.Scatter3d(x=[x], y=[y], z=[z], name=name, mode='markers', marker=go.scatter3d.Marker(size=4))

def draw_sphere():
    step = RESOLUTION // LINES
    theta = linspace(0, 2*pi, RESOLUTION)
    phi = linspace(0, pi, RESOLUTION)
    x = RADIUS * outer(cos(theta),sin(phi))
    y = RADIUS * outer(sin(theta),sin(phi))
    z = RADIUS * outer(ones(RESOLUTION),cos(phi))


    line_params = {'mode': 'lines', 'showlegend': False, 'line': go.scatter3d.Line(color='#CCC', width=2)}
    lon_lines, lat_lines = [], []
    for i in arange(0, x.shape[-1], step):
        lon_lines.append(go.Scatter3d(x=x[i,:], y=y[i,:], z=z[i,:], **line_params))
        lat_lines.append(go.Scatter3d(x=x[:,i], y=y[:,i], z=z[:,i], **line_params))
    
    return lon_lines + lat_lines

In [4]:
def draw_all(transf_matrix, extra_points=None):
    if extra_points is None:
        extra_points = {}
        
    cities = {name: tuple(lla_to_wgs84(lat, lon)) for name, (lat, lon) in CITIES.items()}
    data = draw_sphere() +\
           draw_axes(np.identity(4)) +\
           draw_axes(transf_matrix) +\
           draw_subspace(transf_matrix) +\
           [draw_markers(x, y, z, name) for name, (x, y, z) in cities.items()] +\
           [draw_markers(x, y, z, name) for name, (x, y, z) in extra_points.items()]
    
    a = lla_to_wgs84(CITIES[CITY1][0], CITIES[CITY1][1])
    b = lla_to_wgs84(CITIES[CITY1][0], CITIES[CITY2][1])
    m = (a + b) / 2
    m = m / norm(m) * 2
    
    camera = dict(
        up=dict(x=0, y=0, z=1),
        center=dict(x=0, y=0, z=0),
        eye=dict(x=m[0], y=m[1], z=m[2])
    )
    layout = go.Layout(
        scene=go.layout.Scene(camera=camera),
        title='World and local spaces',
        autosize=False,
        width=1000,
        height=1000,
        margin=go.layout.Margin(l=65, r=50, b=65, t=90)
    )
    fig = go.Figure(data=data, layout=layout)
    iplot(fig)

In [5]:
def project_down(p, T):
    d = norm(T[(0,1,2),(3,3,3)]) # Distance from the origin to the plane
    n = T[(0,1,2),(2,2,2)] / norm(T[(0,1,2),(2,2,2)]) # Normal of the plane (a.k.a. e_3)
    pj = p - (norm(n @ p) - d) * n
    return pj

c1 = CITIES[CITY1]
c2 = CITIES[CITY2]
c3 = c1[0] * 2/3 + c2[0] * 1/3, c1[1] * 2/3 + c2[1] * 1/3

T, T_inv = get_lla_to_xy_matrix(c1, c2)
p = lla_to_wgs84(c3[0], c3[1])
pj = project_down(p, T_inv)

draw_all(T_inv, {'Interpolated City': p, 'Interpolated City projection': pj})

In [6]:
def f(coords, T):
    lat, lon = coords
    p = lla_to_wgs84(lat, lon)
    x, y, z = p
    new_coords = T @ [x, y, z, 1]
    new_coords = new_coords[:2]
    return new_coords

t = 0.5
c1 = CITIES[CITY1]
c2 = CITIES[CITY2]
c3 = c1[0] * (1-t) + c2[0] * t, c1[1] * (1-t) + c2[1] * t
T, T_inv = get_lla_to_xy_matrix(c1, c2)

p1 = f(c1, T)
p2 = f(c2, T)
p3 = f(c3, T)

p1 = round_(p1, 3)
p2 = round_(p2, 3)
p3 = round_(p3, 3)

p1 = p1[:2]
p2 = p2[:2]
p3 = p3[:2]

print(f'Are p1 and p2 oopposite wrt the origin of the new system? {np.all(np.abs(p1+p2) < 1e-5)}')
print(f'Point p3 lat and lon were interpolated between p1 and p2 with t={t}')
print(f'What is the interpolation in the new system? {(p3-p1)/(p2-p1)}')
print(f'How far are p1 and p2 (as per Haversine formula)? {haversine_distance_km(c1[0], c1[1], c2[0], c2[1]):.3f} km')
print(f'How far are p1 and p2 in the new coordinate system? {np.linalg.norm(p1-p2):.3f} km')

Are p1 and p2 oopposite wrt the origin of the new system? True
Point p3 lat and lon were interpolated between p1 and p2 with t=0.5
What is the interpolation in the new system? [0.53325852 0.44302725]
How far are p1 and p2 (as per Haversine formula)? 2440.619 km
How far are p1 and p2 in the new coordinate system? 2425.756 km
